# Enrichment Analysis Notebook

Compares the results of SPINDOCTOR gene set summarization vs statistical ontological enrichment.

Draft: https://docs.google.com/document/d/1H103ux6Dd1_bPM0un4RwutBLcYJx-0ybil2AwlAvG_Q/edit#

## Initial setup

Here we take care of imports, defining the data dictionary for the pandas dataframes

In [16]:
# parameters
#experiment_results = "analysis/enrichment-summary.yaml"

experiment_results = "../enrichgpt-results/results/enrichment-summary.yaml"

In [3]:
import yaml
from yaml import Loader
import pandas as pd
from oaklib import get_adapter
from oaklib.datamodels.vocabulary import IS_A, PART_OF
from ontogpt.evaluation.enrichment.eval_enrichment import EvalEnrichment
go = get_adapter("sqlite:obo:go")
hgnc = get_adapter("sqlite:obo:hgnc")

/Users/marcin/.pyenv/versions/3.10.11/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[nltk_data] Downloading package punkt to /Users/marcin/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/marcin/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /Users/marcin/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to /Users/marcin/nltk_data...
[nltk_data]   Package words is already up-to-date!


In [4]:
#from ontogpt.utils.gene_set_utils import populate_ids_and_symbols, GeneSet
#ee = EvalEnrichment()
#ee.ontology = go
#ee.load_annotations("../tests/input/genes2go.tsv.gz")

In [5]:
# data dictionary
MODEL = "model"
METHOD = "method"
HAS_TOP_HIT = "has top hit"
IN_TOP_5 = "in top 5"
IN_TOP_10 = "in top 10"
RANK = "rank"
SIZE_OVERLAP = "size overlap"
SIMILARITY = "similarity"
NR_SIZE_OVERLAP = "nr size overlap"
NR_SIMILARITY = "nr similarity"
GENESET = "geneset"
SOURCE_GENESET = "source geneset"
GENESET_SIZE = "geneset_size"
TRUNCATION_FACTOR = "truncation factor"
NUM_TERMS = "num terms"
NUM_GO_TERMS = "num GO terms"
NUM_UNPARSED = "num unparsed"
TERM_IDS = "term ids"
GO_TERM_IDS = "go term ids"
GO_TERM_P_VALUES = "go term p values"
MAX_P_VALUE = "max p value"
MIN_P_VALUE = "min p value"
MEAN_P_VALUE = "mean p value"
PROPOTION_SIGNIFICANT = "proportion significant"
NOVEL = "novel"
NOVEL_LABELS = "novel labels"
NUM_NOVEL = "num novel"
GENE_RANDOMIZATION_FACTOR = "gene_randomization_factor"


TURBO = "gpt-3.5-turbo"
DAVINCI = "text-davinci-003"
MODELS = [TURBO, DAVINCI]

In [6]:
from ontogpt.evaluation.enrichment.eval_enrichment import GeneSetComparison

In [10]:
# assumes comparisons have been run and concatenated (see Makefile) 
def load_comparisons():
    with open(f"../{experiment_results}") as f:
        obj = yaml.load(f, Loader)
        comps = [GeneSetComparison(**x) for x in obj]
        return comps

In [17]:
comps = load_comparisons()

In [18]:

def filter_redundant(term_ids):
    """
    find leaf nodes in a set of term ids
    """
    cumulative_ancs = set()
    visited = set()
    for t in term_ids:
        visited.add(t)
        if t in cumulative_ancs:
            # a descendant of t has been encountered
            continue
        ancs = list(go.ancestors(t, [IS_A, PART_OF]))
        cumulative_ancs.update(ancs)
        if (visited-{t}).intersection(ancs):
            # t is a descendant of a term that has been encountered
            continue
        yield t

# test
list(filter_redundant(["GO:0005773", "GO:0005634", "GO:0031965", "GO:0008150"]))

['GO:0005773', 'GO:0005634', 'GO:0008150']

In [19]:
import statistics
import re
def eval_payload(comp, payload, expected, closure):
    """
    Create a dataframe row from a payload in a comparison
    """
    expected_nr_ids = list(filter_redundant(expected.term_ids))
    name = comp.name
    model = payload.model
    method = payload.method
    if not model:
        model = "N/A"
    tf = payload.truncation_factor
    if not tf:
        tf = 1.0
    unparsed_term_ids = [t for t in payload.term_ids if not re.match(r'^\S+:w+$', t)]
    go_term_ids = [t for t in payload.term_ids if t.startswith("GO:")]
    nr_term_ids = list(filter_redundant(go_term_ids))
    obj = {MODEL: model, METHOD: method, GENESET: name, TRUNCATION_FACTOR: tf}
    name_toks = name.split("-")
    obj[SOURCE_GENESET] = "-".join(name_toks[0:-1])
    obj[GENE_RANDOMIZATION_FACTOR] = int(name_toks[-1])
    if not expected.term_ids:
        #print(f"Nothing expected for {name}")
        # top_term_id = "FAKE:123"
        return
    else:
        top_term_id = expected.term_ids[0]
    obj[HAS_TOP_HIT] = top_term_id in payload.term_ids
    in_top_5 = False
    in_top_10 = False
    if top_term_id in payload.term_ids:
        rank = payload.term_ids.index(top_term_id)
        obj[RANK] = rank
        in_top_5 = rank < 5
        in_top_10 = rank < 10
    obj[IN_TOP_5] = in_top_5
    obj[IN_TOP_10] = in_top_10
    overlap = set(go_term_ids).intersection(expected.term_ids)
    obj[SIZE_OVERLAP] = len(overlap)
    nr_overlap = set(nr_term_ids).intersection(expected_nr_ids)
    obj[NR_SIZE_OVERLAP] = len(nr_overlap)
    size_union = len(set(go_term_ids).union(expected.term_ids))
    if size_union:
        obj[SIMILARITY] = len(overlap) / len(set(go_term_ids).union(expected.term_ids))
    nr_size_union = len(set(nr_term_ids).union(expected_nr_ids))
    if nr_size_union:
        obj[NR_SIMILARITY] = len(nr_overlap) / len(set(nr_term_ids).union(expected_nr_ids))
    obj['number_of_terms'] = len(payload.term_ids)
    obj[NUM_GO_TERMS] = len(go_term_ids)
    obj[GENESET_SIZE] = len(comp.gene_symbols)
    obj[TERM_IDS] = payload.term_ids
    obj['term_strings'] = payload.term_strings
    obj[GO_TERM_IDS] = go_term_ids
    obj[NUM_TERMS] = len(payload.term_ids)
    obj[NUM_UNPARSED] = len(unparsed_term_ids)
    p_vals = []
    for t in go_term_ids:
        p_val = 1.0
        for e in expected.enrichment_results:
            if e.class_id == t:
                p_val = e.p_value_adjusted
                break
        p_vals.append(p_val)
    obj[GO_TERM_P_VALUES] = p_vals
    if p_vals:
        obj[MAX_P_VALUE] = max(p_vals)
        obj[MIN_P_VALUE] = min(p_vals)
        obj[MEAN_P_VALUE] = statistics.mean(p_vals)
        obj[PROPOTION_SIGNIFICANT] = len([v for v in p_vals if v<=0.05]) / len(p_vals)
    novel = []
    novel_labels = []
    # enriched_terms = [e.class_id for e in expected.enrichment_results]
    for t in go_term_ids:
        if t not in closure:
            novel.append(t)
            novel_labels.append(go.label(t))
    obj[NOVEL] = novel
    obj[NOVEL_LABELS] = novel_labels
    obj[NUM_NOVEL] = len(novel)
    return obj

objs = []
for comp in comps:
    expected = comp.payloads["standard"]
    closure = comp.payloads["closure"].term_ids
    #gene_set = GeneSet(name=comp.name, gene_symbols=comp.gene_symbols)
    #populate_ids_and_symbols(gene_set, hgnc)
    
    for method, payload in comp.payloads.items():
        obj = eval_payload(comp, payload, expected, closure)
        if obj:
            objs.append(obj)
            # temp
            if not obj[METHOD]:
                obj[METHOD] = method
df = pd.DataFrame(objs)
df.to_csv("enr.csv")
df

model                method                  geneset  \
0     gpt-3.5-turbo           no_synopsis                    EDS-0   
1     gpt-3.5-turbo           no_synopsis                    EDS-0   
2     gpt-3.5-turbo  ontological_synopsis                    EDS-0   
3     gpt-3.5-turbo  ontological_synopsis                    EDS-0   
4     gpt-3.5-turbo    narrative_synopsis                    EDS-0   
...             ...                   ...                      ...   
2409            N/A              standard  tf-downreg-colorectal-1   
2410            N/A  standard_no_ontology  tf-downreg-colorectal-1   
2411            N/A                random  tf-downreg-colorectal-1   
2412            N/A            rank_based  tf-downreg-colorectal-1   
2413            N/A               closure  tf-downreg-colorectal-1   

      truncation factor         source geneset  gene_randomization_factor  \
0                   1.0                    EDS                          0   
1                   1.0                    EDS                          0   
2                   1.0                    EDS                          0   
3                   1.0                    EDS                          0   
4                   1.0                    EDS                          0   
...                 ...                    ...                        ...   
2409                1.0  tf-downreg-colorectal                          1   
2410                1.0  tf-downreg-colorectal                          1   
2411                1.0  tf-downreg-colorectal                          1   
2412                1.0  tf-downreg-colorectal                          1   
2413                1.0  tf-downreg-colorectal                          1   

      has top hit   rank  in top 5  in top 10  ...  num terms  num unparsed  \
0            True    1.0      True       True  ...          3             3   
1            True    2.0      True       True  ...          6             6   
2            True    0.0      True       True  ...          4             4   
3            True    0.0      True       True  ...          5             5   
4           False    NaN     False      False  ...          7             7   
...           ...    ...       ...        ...  ...        ...           ...   
2409         True    0.0      True       True  ...        180           180   
2410        False    NaN     False      False  ...         40            40   
2411        False    NaN     False      False  ...         42            42   
2412        False    NaN     False      False  ...         46            46   
2413         True  505.0     False      False  ...       3523          3523   

                                       go term p values  max p value  \
0     [3.341122685366184e-06, 5.591343976855226e-11,...     0.000321   
1     [3.341122685366184e-06, 3.4271478353194616e-06...     1.000000   
2     [5.591343976855226e-11, 3.341122685366184e-06,...     1.000000   
3     [5.591343976855226e-11, 1.0, 2.2177237867319e-...     1.000000   
4     [1.0, 3.341122685366184e-06, 1.0, 1.0, 1.0, 1....     1.000000   
...                                                 ...          ...   
2409  [2.463439488461684e-28, 2.511460888299925e-28,...     0.047670   
2410  [1.0670949536417977e-21, 6.368123603602858e-19...     1.000000   
2411  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 6.26342211...     1.000000   
2412  [4.966218259085737e-14, 1.0, 1.0, 1.0, 1.0, 6....     1.000000   
2413  [1.0, 1.0, 1.0, 3.405746031985595e-10, 1.0, 1....     1.000000   

       min p value  mean p value  proportion significant  \
0     5.591344e-11      0.000108                1.000000   
1     5.591344e-11      0.500001                0.500000   
2     5.591344e-11      0.250081                0.750000   
3     5.591344e-11      0.200065                0.800000   
4     3.341123e-06      0.857143                0.142857   
...            ...           ...                     ...   
2409  2.463439

The above data frame has one row per run of a method

In [20]:
df[[MODEL, METHOD]].drop_duplicates()

model                method
0      gpt-3.5-turbo           no_synopsis
2      gpt-3.5-turbo  ontological_synopsis
4      gpt-3.5-turbo    narrative_synopsis
6   text-davinci-003           no_synopsis
8   text-davinci-003  ontological_synopsis
10  text-davinci-003    narrative_synopsis
12               N/A              standard
13               N/A  standard_no_ontology
14               N/A                random
15               N/A            rank_based
16               N/A               closure

In [21]:
df[[SOURCE_GENESET]].drop_duplicates()

source geneset
0                                              EDS
34                                              FA
68                           HALLMARK_ADIPOGENESIS
102                   HALLMARK_ALLOGRAFT_REJECTION
136                     HALLMARK_ANDROGEN_RESPONSE
...                                            ...
2244                                    peroxisome
2278                                      progeria
2312  regulation of presynaptic membrane potential
2346                                sensory ataxia
2380                         tf-downreg-colorectal

[71 rows x 1 columns]

In [22]:
df[[SOURCE_GENESET, GENESET_SIZE]].drop_duplicates().style.hide_index()

/var/folders/lm/hg0p5znd1hd5yc5lml35j6lh0000gn/T/ipykernel_20660/3852654709.py:1: FutureWarning: this method is deprecated in favour of `Styler.hide(axis="index")`
  df[[SOURCE_GENESET, GENESET_SIZE]].drop_duplicates().style.hide_index()


In [23]:
df[[MODEL, METHOD]].drop_duplicates().style.hide_index()

/var/folders/lm/hg0p5znd1hd5yc5lml35j6lh0000gn/T/ipykernel_20660/2185383538.py:1: FutureWarning: this method is deprecated in favour of `Styler.hide(axis="index")`
  df[[MODEL, METHOD]].drop_duplicates().style.hide_index()


## Subset Analysis

In [24]:
from collections import defaultdict
go = get_adapter("sqlite:obo:go")
subsets = list(go.subsets())
subsets_by_term = defaultdict(list)
for subset in subsets:
    members = [m for m in go.subset_members(subset) if m.startswith("GO:")]
    for t in members:
        subsets_by_term[t].append(subset)
    members_ancs = go.ancestors(members)
    anc_subset = f"anc_of_{subset}"
    for a in members_ancs:
        if a not in members:
            subsets_by_term[a].append(anc_subset)

In [25]:
objs = []
for row in df.to_dict(orient="records"):
    for t in row[GO_TERM_IDS]:
        obj = {MODEL: row.get(MODEL), METHOD: row.get(METHOD) , "term": t, "label": go.label(t)}
        for s in subsets_by_term.get(t, []):
            obj[s] = 1
        objs.append(obj)
print(len(objs))
subsets_df=pd.DataFrame(objs) 
pd.set_option('display.max_rows', 10)
subsets_df

756445


model       method        term  \
0       gpt-3.5-turbo  no_synopsis  GO:0030198   
1       gpt-3.5-turbo  no_synopsis  GO:0030199   
2       gpt-3.5-turbo  no_synopsis  GO:0006024   
3       gpt-3.5-turbo  no_synopsis  GO:0030198   
4       gpt-3.5-turbo  no_synopsis  GO:0043062   
...               ...          ...         ...   
756440            N/A      closure  GO:0032106   
756441            N/A      closure  GO:0032109   
756442            N/A      closure  GO:0045848   
756443            N/A      closure  GO:2001248   
756444            N/A      closure  GO:2001250   

                                                    label  goslim_chembl  \
0                       extracellular matrix organization            1.0   
1                            collagen fibril organization            NaN   
2                  glycosaminoglycan biosynthetic process            NaN   
3                       extracellular matrix organization            1.0   
4                    extracellular structure organization            NaN   
...                                                   ...            ...   
756440  positive regulation of response to extracellul...            NaN   
756441  positive regulation of response to nutrient le...            NaN   
756442        positive regulation of nitrogen utilization            NaN   
756443           regulation of ammonia assimilation cycle            NaN   
756444  positive regulation of ammonia assimilation cycle            NaN   

        goslim_generic  goslim_drosophila  goslim_pir  anc_of_goslim_chembl  \
0                  1.0                1.0         NaN                   NaN   
1                  NaN                NaN         NaN                   NaN   
2                  NaN                NaN         NaN                   NaN   
3                  1.0                1.0         NaN                   NaN   
4                  NaN                NaN         1.0                   1.0   
...                ...                ...         ...                   ...   
756440             NaN                NaN         NaN                   NaN   
756441             NaN                NaN         NaN                   NaN   
756442             NaN                NaN         NaN                   NaN   
756443             NaN                NaN         NaN                   NaN   
756444             NaN                NaN         NaN                   NaN   

        anc_of_goslim_generic  ...  anc_of_goslim_flybase_ribbon  \
0                         NaN  ...                           NaN   
1                         NaN  ...                           NaN   
2                         NaN  ...                           NaN   
3                         NaN  ...                           NaN   
4                         1.0  ...                           NaN   
...                       ...  ...                           ...   
756440                    NaN  ...                           NaN   
756441                    NaN  ...                           NaN   
756442                    NaN  ...                           NaN   
756443                    NaN  ...                           NaN   
756444                    NaN  ...                           NaN   

        anc_of_goslim_agr  goslim_mouse  anc_of_goslim_plant  \
0                     NaN           NaN                  NaN   
1                     NaN           NaN                  NaN   
2                     NaN           NaN                  NaN   
3                     NaN           NaN                  NaN   
4                     NaN           NaN                  NaN   
...                   ...           ...                  ...   
756440                NaN           NaN                  NaN   
756441                NaN           NaN                  NaN   
756442                NaN           NaN                  NaN   
756443                NaN           NaN                  NaN   
756444                NaN       

In [26]:
subsets_df.fillna(0).groupby([MODEL, METHOD]).mean(numeric_only=True).style.highlight_max(axis=1, props='font-weight:bold').format(precision=3)

In [27]:
subsets_cols =  [MODEL, METHOD, "goslim_generic", "anc_of_goslim_generic", "goslim_agr", "anc_of_goslim_agr"]
subsets_grouped = subsets_df.fillna(0).groupby([MODEL, METHOD])[subsets_cols]
means = subsets_grouped.mean(numeric_only=True)
means["closure_of_goslim_generic"] = means["goslim_generic"] + means["anc_of_goslim_generic"]
means["closure_of_goslim_agr"] = means["goslim_agr"] + means["anc_of_goslim_agr"]
means.style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)

In [28]:
means.sort_values("closure_of_goslim_generic", ascending=False).style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)

In [33]:
def agg_table(this_df, cols, exclude=[None]):
    qcols = [MODEL, METHOD] + cols
    agg_df = this_df[qcols].groupby([MODEL, METHOD]).mean(numeric_only=True)
    for x in exclude:
        agg_df= agg_df.query(f"method != '{x}'")
    return agg_df.style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)


In [32]:
agg_table(df, [NUM_GO_TERMS, SIZE_OVERLAP, NR_SIZE_OVERLAP], ["standard"])

In [30]:
means[["anc_of_goslim_generic", "anc_of_goslim_agr"]].sort_values("anc_of_goslim_agr", ascending=True).style.highlight_min(axis=0, props='font-weight:bold').format(precision=3)

In [165]:
# Reset the index of the pivoted DataFrame to have 'profession' as a column
#subsets_df = subsets_df.fillna(0).groupby([MODEL, METHOD])[subsets_cols].mean(numeric_only=True).reset_index()

# Melt the DataFrame to have 'category', 'profession', and 'percentage' columns
#melted_df = subsets_df.melt(id_vars=[MODEL, METHOD], var_name='subset', value_name='proportion')
#melted_df["mm"] = melted_df[MODEL] + melted_df[METHOD]
#melted_df
# Create a bar plot using Seaborn
#plt.figure(figsize=(10, 6))
#sns.barplot(x='subset', y='proportion', hue="mm", data=melted_df)
#plt.title('Subsets by method')
#plt.xlabel('Subset')
#plt.ylabel('Proportion')
#plt.legend(title='Subsets')
#plt.show()

## Evaluation

In [34]:

pd.options.display.precision = 2
pd.set_option("display.precision", 2)

In [35]:
eval_summary_cols = [HAS_TOP_HIT, IN_TOP_5, IN_TOP_10, SIZE_OVERLAP, SIMILARITY, NUM_TERMS, NUM_GO_TERMS, NR_SIZE_OVERLAP, NR_SIMILARITY, MEAN_P_VALUE, MIN_P_VALUE, MAX_P_VALUE, PROPOTION_SIGNIFICANT, NUM_NOVEL]
agg_table(df, eval_summary_cols)

In [36]:
agg_table(df, [PROPOTION_SIGNIFICANT, NUM_GO_TERMS, HAS_TOP_HIT, NUM_NOVEL], ["standard", "standard_no_ontology", "random", "rank_based"])
#means.query("method != 'standard'").style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)

In [37]:
df_no_perturb = df.query(f"{GENE_RANDOMIZATION_FACTOR} == 0")
agg_table(df_no_perturb, [PROPOTION_SIGNIFICANT, NUM_GO_TERMS, HAS_TOP_HIT, NUM_NOVEL], ["closure", "standard", "standard_no_ontology", "random", "rank_based"])


## Maximums

In [38]:
df[[MODEL, METHOD] + eval_summary_cols].groupby([MODEL, METHOD]).max(numeric_only=True).style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)

### Effect of truncation

Larger gene sets penalize annotation-based GPT methods due to the necessity to truncate to fit in the window size.



In [41]:
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(color_codes=True)
np.random.seed(sum(map(ord, "regression")))
sns.lmplot(x=GENESET_SIZE, y=TRUNCATION_FACTOR, data=df.query("method=='ontological_synopsis'"))
plt.show()

In [42]:
dftups = [(method, df.query(f"method=='{method}'")) for method in ["ontological_synopsis", "narrative_synopsis"]]
for m, mdf in dftups:
    mdf.assign(dataset=m)
concatenated = pd.concat([mdf.assign(dataset=m) for m, mdf in dftups])
sns.scatterplot(x=GENESET_SIZE, y=TRUNCATION_FACTOR, data=concatenated, style='dataset', hue='model')

<Axes: xlabel='geneset_size', ylabel='truncation factor'>

In [43]:
df.query(f"{GENESET_SIZE} < 50")[[SOURCE_GENESET]].drop_duplicates()

source geneset
0                                              EDS
34                                              FA
170                          HALLMARK_ANGIOGENESIS
238                        HALLMARK_APICAL_SURFACE
714                    HALLMARK_HEDGEHOG_SIGNALING
...                                            ...
2244                                    peroxisome
2278                                      progeria
2312  regulation of presynaptic membrane potential
2346                                sensory ataxia
2397                         tf-downreg-colorectal

[25 rows x 1 columns]

In [44]:
df_small = df.query(f"{GENESET_SIZE} < 50")
means = df_small[[MODEL, METHOD] + eval_summary_cols].groupby(['model', 'method']).mean(numeric_only=True)
means

has top hit  in top 5  in top 10  \
model            method                                                   
N/A              closure                      1.00      0.04       0.09   
                 random                       0.00      0.00       0.00   
                 rank_based                   0.04      0.04       0.04   
                 standard                     1.00      1.00       1.00   
                 standard_no_ontology         0.63      0.54       0.57   
...                                            ...       ...        ...   
gpt-3.5-turbo    no_synopsis                  0.20      0.18       0.20   
                 ontological_synopsis         0.34      0.34       0.34   
text-davinci-003 narrative_synopsis           0.12      0.12       0.12   
                 no_synopsis                  0.12      0.11       0.12   
                 ontological_synopsis         0.22      0.12       0.17   

                                       size overlap  similarity  num terms  \
model            method                                                      
N/A              closure                     132.61    7.95e-02    2389.76   
                 random                        1.41    7.41e-03      26.07   
                 rank_based                    2.85    1.70e-02      26.72   
                 standard                    132.61    9.83e-01     135.43   
                 standard_no_ontology         28.80    2.14e-01      38.37   
...                                             ...         ...        ...   
gpt-3.5-turbo    no_synopsis                   2.45    2.44e-02       5.27   
                 ontological_synopsis          2.27    3.10e-02       5.35   
text-davinci-003 narrative_synopsis            1.18    1.07e-02      11.34   
                 no_synopsis                   1.00    7.48e-03       7.36   
                 ontological_synopsis          2.51    2.36e-02      12.59   

                                       num GO terms  nr size overlap  \
model            method                                                
N/A              closure                    2346.59             3.37   
                 random                       26.07             0.26   
                 rank_based                   26.72             0.33   
                 standard                    132.61            15.91   
                 standard_no_ontology         38.37             5.65   
...                                             ...              ...   
gpt-3.5-turbo    no_synopsis                   4.33             0.71   
                 ontological_synopsis          3.90             0.77   
text-davinci-003 narrative_synopsis            3.35             0.35   
                 no_synopsis                   2.62             0.28   
                 ontological_synopsis          7.91             0.51   

                                       nr similarity  mean p value  \
model            method                                              
N/A              closure                    2.25e-02      9.15e-01   
                 random                     6.61e-03      9.54e-01   
                 rank_based                 9.68e-03      9.11e-01   
                 standard                   9.71e-01      8.28e-03   
                 standard_no_ontology       1.92e-01      2.96e-01   
...                                              ...           ...   
gpt-3.5-turbo    no_synopsis                4.07e-02      4.27e-01   
                 ontological_synopsis       5.39e-02      3.90e-01   
text-davinci-003 narrative_synopsis         1.99e-02      6.75e-01   
                 no_synopsis                1.59e-02      5.95e-01   
                 ontological_synopsis       2.53e-02      6.63e-01   

                                       min p value  max p value  \
model            method                                           
N/A              closure                  2.59e-04         1.00   

In [45]:
means.query("method != 'standard'").style.highlight_max(axis=0, props='font-weight:bold').format(precision=3)

In [46]:
agg_table(df_small, [PROPOTION_SIGNIFICANT, NUM_GO_TERMS, HAS_TOP_HIT, NUM_NOVEL], ["standard", "standard_no_ontology", "random", "rank_based"])

## Looking at individual gene sets

In [47]:

def terms_summary(df, max_rows=9999):
    term_dict = {}
    n = 0
    for _, row in df.iterrows():
        n += 1
        if n > max_rows:
            break
        model = row['model'] 
        if "turbo" in model:
            model = "turbo"
        elif "davinci" in model:
            model = "dav"
        else:
            model = ""
        method = str(row['method']).replace('_', ' ')
        if method in ["closure", "rank_based", "random"]:
            continue
        mm = f"{model} {method}"
        if method == "standard":
            nr_term_ids = list(filter_redundant(row[TERM_IDS]))
        else:
            nr_term_ids = None
        for ix, t_id in enumerate(row[TERM_IDS]):
            if t_id not in term_dict:
                t = {"id": t_id, "label": go.label(t_id), "redundant": False}
                term_dict[t_id] = t
            else:
                t = term_dict[t_id]
            t[mm] = ix
            if nr_term_ids and t_id not in nr_term_ids:
                t["redundant"] = True
    objs = list(term_dict.values())
    return pd.DataFrame(objs)

### Peroxisome

In [48]:
peroxisome = df.query(f"{GENESET} == 'peroxisome-0'").sort_values("similarity", ascending=False)
peroxisome[[MODEL, METHOD] + eval_summary_cols]

model                method  has top hit  in top 5  \
2256               N/A              standard         True      True   
2257               N/A  standard_no_ontology         True     False   
2260               N/A               closure         True      True   
2252  text-davinci-003  ontological_synopsis        False     False   
2253  text-davinci-003  ontological_synopsis         True     False   
...                ...                   ...          ...       ...   
2254  text-davinci-003    narrative_synopsis        False     False   
2255  text-davinci-003    narrative_synopsis        False     False   
2247     gpt-3.5-turbo  ontological_synopsis        False     False   
2258               N/A                random        False     False   
2259               N/A            rank_based        False     False   

      in top 10  size overlap  similarity  num terms  num GO terms  \
2256       True            62        1.00         62            62   
2257      False            15        0.22         21            21   
2260       True            62        0.19        419           391   
2252      False             5        0.08         10             6   
2253       True             4        0.06         10             6   
...         ...           ...         ...        ...           ...   
2254      False             0        0.00          8             0   
2255      False             0        0.00          3             0   
2247      False             0        0.00          3             1   
2258      False             0        0.00          8             8   
2259      False             0        0.00          8             8   

      nr size overlap  nr similarity  mean p value  min p value  max p value  \
2256               10           1.00      5.64e-03     1.98e-16         0.04   
2257                7           0.41      2.89e-01     1.98e-16         1.00   
2260                7           0.14      8.02e-01     1.98e-16         1.00   
2252                4           0.33      1.73e-01     2.87e-04         1.00   
2253                2           0.15      3.33e-01     1.98e-16         1.00   
...               ...            ...           ...          ...          ...   
2254                0           0.00           NaN          NaN          NaN   
2255                0           0.00           NaN          NaN          NaN   
2247                0           0.00      1.00e+00     1.00e+00         1.00   
2258                0           0.00      1.00e+00     1.00e+00         1.00   
2259                0           0.00      1.00e+00     1.00e+00         1.00   

      proportion significant  num novel  
2256                    1.00          0  
2257                    0.71          0  
2260                    0.20          0  
2252                    0.83          0  
2253                    0.67          0  
...                      ...        ...  
2254                     NaN          0  
2255                     NaN          0  
2247                    0.00          1  
2258                    0.00          7  
2259                    0.00          1  

[17 rows x 16 columns]

In [49]:
# terms_summary(peroxisome).style.highlight_min(axis=1, props='font-weight:bold', numeric_only=True)
terms_summary(peroxisome)

id                                              label  redundant  \
0    GO:0006625                    protein targeting to peroxisome      False   
1    GO:0072663  establishment of protein localization to perox...       True   
2    GO:0072662                 protein localization to peroxisome       True   
3    GO:0015919                     peroxisomal membrane transport      False   
4    GO:0043574                              peroxisomal transport       True   
..          ...                                                ...        ...   
112  GO:0016020                                           membrane      False   
113  GO:0005829                                            cytosol      False   
114  GO:0005634                                            nucleus      False   
115  GO:0005654                                        nucleoplasm      False   
116  GO:0046872                                  metal ion binding      False   

      standard   standard no ontology  dav ontological synopsis  \
0          0.0                   10.0                       8.0   
1          1.0                    NaN                       NaN   
2          2.0                    NaN                       NaN   
3          3.0                    NaN                       NaN   
4          4.0                    NaN                       NaN   
..         ...                    ...                       ...   
112        NaN                    NaN                       NaN   
113        NaN                    NaN                       NaN   
114        NaN                    NaN                       NaN   
115        NaN                    NaN                       NaN   
116        NaN                    NaN                       NaN   

     turbo no synopsis  turbo narrative synopsis  turbo ontological synopsis  \
0                  NaN                       NaN                         NaN   
1                  NaN                       NaN                         NaN   
2                  NaN                       NaN                         NaN   
3                  NaN                       NaN                         NaN   
4                  NaN                       NaN                         NaN   
..                 ...                       ...                         ...   
112                NaN                       NaN                         NaN   
113                NaN                       NaN                         NaN   
114                NaN                       NaN                         NaN   
115                NaN                       NaN                         NaN   
116                NaN                       NaN                         NaN   

     dav no synopsis  dav narrative synopsis   rank based  
0                NaN                     NaN          NaN  
1                NaN                     NaN          NaN  
2                NaN                     NaN          NaN  
3                NaN                     NaN          NaN  
4                NaN                     NaN          NaN  
..               ...                     ...          ...  
112              NaN                     NaN          3.0  
113              NaN                     NaN          4.0  
114              NaN                     NaN          5.0  
115              NaN                     NaN          6.0  
116              NaN                     NaN          7.0  

[117 rows x 12 columns]

## Sensory Ataxia

In [50]:
ataxia = df.query(f"{GENESET} == 'sensory ataxia-0'").sort_values("similarity", ascending=False)
ataxia[[MODEL, METHOD] + eval_summary_cols]                                                  

model                method  has top hit  in top 5  \
2358               N/A              standard         True      True   
2359               N/A  standard_no_ontology        False     False   
2348     gpt-3.5-turbo  ontological_synopsis         True      True   
2349     gpt-3.5-turbo  ontological_synopsis         True      True   
2351     gpt-3.5-turbo    narrative_synopsis        False     False   
...                ...                   ...          ...       ...   
2357  text-davinci-003    narrative_synopsis        False     False   
2356  text-davinci-003    narrative_synopsis        False     False   
2353  text-davinci-003           no_synopsis        False     False   
2352  text-davinci-003           no_synopsis        False     False   
2354  text-davinci-003  ontological_synopsis        False     False   

      in top 10  size overlap  similarity  num terms  num GO terms  \
2358       True             9        1.00          9             9   
2359      False             3        0.30          4             4   
2348       True             2        0.20          5             3   
2349       True             2        0.18          7             4   
2351      False             1        0.11          5             1   
...         ...           ...         ...        ...           ...   
2357      False             0        0.00         11             4   
2356      False             0        0.00          8             2   
2353      False             0        0.00          5             3   
2352      False             0        0.00          5             3   
2354      False             0        0.00          9             6   

      nr size overlap  nr similarity  mean p value  min p value  max p value  \
2358                3           1.00          0.01     1.95e-05         0.04   
2359                1           0.20          0.26     3.13e-04         1.00   
2348                2           0.67          0.33     1.95e-05         1.00   
2349                2           0.40          0.50     1.95e-05         1.00   
2351                1           0.33          0.03     2.80e-02         0.03   
...               ...            ...           ...          ...          ...   
2357                0           0.00          1.00     1.00e+00         1.00   
2356                0           0.00          1.00     1.00e+00         1.00   
2353                0           0.00          1.00     1.00e+00         1.00   
2352                0           0.00          1.00     1.00e+00         1.00   
2354                0           0.00          1.00     1.00e+00         1.00   

      proportion significant  num novel  
2358                    1.00          0  
2359                    0.75          0  
2348                    0.67          0  
2349                    0.50          0  
2351                    1.00          0  
...                      ...        ...  
2357                    0.00          1  
2356                    0.00          0  
2353                    0.00          1  
2352                    0.00          0  
2354                    0.00          0  

[17 rows x 16 columns]

In [51]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)


In [52]:
ataxia[[MODEL, METHOD, GO_TERM_IDS, NOVEL_LABELS]]

model                method  \
2358               N/A              standard   
2359               N/A  standard_no_ontology   
2348     gpt-3.5-turbo  ontological_synopsis   
2349     gpt-3.5-turbo  ontological_synopsis   
2351     gpt-3.5-turbo    narrative_synopsis   
2350     gpt-3.5-turbo    narrative_synopsis   
2347     gpt-3.5-turbo           no_synopsis   
2355  text-davinci-003  ontological_synopsis   
2362               N/A               closure   
2361               N/A            rank_based   
2360               N/A                random   
2346     gpt-3.5-turbo           no_synopsis   
2357  text-davinci-003    narrative_synopsis   
2356  text-davinci-003    narrative_synopsis   
2353  text-davinci-003           no_synopsis   
2352  text-davinci-003           no_synopsis   
2354  text-davinci-003  ontological_synopsis   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                go term ids  \
2358                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           [GO:0042552, GO:0008366, GO:0007272, GO:0007422, GO:0014037, GO:0010001, GO:0032287, GO:0006264, GO:0042063]   
2359                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [53]:
terms_summary(ataxia)

id  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0042552   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0008366   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0007272   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0007422   
4                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0014037   
5                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0010001   
6                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0032287   
7                                                                                                                                                                                                                                                                                                                                                                                                                                                    GO:0006264   
8                                                                                                                                                                                                                                                                                                                                                                                                 

In [54]:
def retrieve_payload(geneset, method):
    for comp in comps:
        if comp.name == geneset:
            return comp.payloads[method]

In [55]:
print(retrieve_payload("sensory ataxia-0", "gpt-3.5-turbo.ontological_synopsis").response_text)

KeyError: 'gpt-3.5-turbo.ontological_synopsis'

In [56]:
print(retrieve_payload("sensory ataxia-0", "gpt-3.5-turbo.narrative_synopsis").response_text)

KeyError: 'gpt-3.5-turbo.narrative_synopsis'

In [57]:
print(retrieve_payload("sensory ataxia-0", "gpt-3.5-turbo.no_synopsis").response_text)

KeyError: 'gpt-3.5-turbo.no_synopsis'

## Endocytosis

In [58]:
endocytosis = df.query(f"{GENESET} == 'endocytosis-0'").sort_values("similarity", ascending=False)
terms_summary(endocytosis)

id  \
0                                                                                                                                                                                                                                                                                                                                                  GO:0006907   
1                                                                                                                                                                                                                                                                                                                                                  GO:0006897   
2                                                                                                                                                                                                                                                                                                                                                  GO:0044351   
3                                                                                                                                                                                                                                                                                                                                                  GO:0016192   
4                                                                                                                                                                                                                                                                                                                                                  GO:0030100   
5                                                                                                                                                                                                                                                                                                                                                  GO:0006810   
6                                                                                                                                                                                                                                                                                                                                                  GO:0051234   
7                                                                                                                                                                                                                                                                                                                                                  GO:0045807   
8                                                                                                                                                                                                                                                                                                                                                  GO:0060627   
9                                                                                                                                                                                                                                                                                                                                                  GO:0051179   
10                                                                                                                                                                                                                                                                                                                                                 GO:0031410   
11                                                                                                             

In [59]:
print(retrieve_payload("endocytosis-0", "gpt-3.5-turbo.narrative_synopsis").prompt)

KeyError: 'gpt-3.5-turbo.narrative_synopsis'

In [60]:
print(retrieve_payload("endocytosis-0", "gpt-3.5-turbo.narrative_synopsis").response_text)

KeyError: 'gpt-3.5-turbo.narrative_synopsis'

In [61]:
print(retrieve_payload("endocytosis-0", "gpt-3.5-turbo.ontological_synopsis").prompt)

KeyError: 'gpt-3.5-turbo.ontological_synopsis'

## Hallucinations

In [62]:
def hallucinatons(df, model):
    novel_term_map = defaultdict(dict)
    for _, row in df.iterrows():
        gs = row[GENESET]
        #if not gs.endswith("-0"):
        #    continue
        gs = gs.replace("-0", "")
        for lbl in row[NOVEL_LABELS]:
            if row[MODEL] != model:
                continue
            m = row[METHOD]
            novel_term_map[lbl]["NAME"] = lbl
            if gs not in novel_term_map[lbl]:
                novel_term_map[lbl][m] = []
            novel_term_map[lbl][m].append(gs)
    novel_df = pd.DataFrame(novel_term_map.values())
    return novel_df

In [63]:
novel_df_turbo = hallucinatons(df, TURBO)
novel_df_turbo

NAME  \
0                                                          regulation of collagen metabolic process   
1                                                           post-translational protein modification   
2                                                                                   protein folding   
3                                                  positive regulation of fatty acid beta-oxidation   
4                                                                       obsolete electron transport   
5                                                                                       cell growth   
6                                           obsolete transcription factor activity, protein binding   
7                                                                          interleukin-2 production   
8                                                                     type II interferon production   
9                                                                   regulation of protein stability   
10                                                                           platelet degranulation   
11                                                                   regulation of bone development   
12                                                                   proteoglycan metabolic process   
13                         regulation of transforming growth factor beta receptor signaling pathway   
14                                                           regulation of mitotic nuclear division   
15                                       obsolete calcium-dependent cell adhesion molecule activity   
16                                          regulation of signal transduction by p53 class mediator   
17                                                              modulation by virus of host process   
18                                                          regulation of glucose metabolic process   
19                                                                       protein kinase C signaling   
20                                                       positive regulation of MAP kinase activity   
21                                                  regulation of B cell receptor signaling pathway   
22                                                                         obsolete cytochrome P450   
23                                                                    obsolete cell surface binding   
24                                                        calcium-dependent protein kinase activity   
25                                                                calcium-dependent ATPase activity   
26                                                                     acetyl-CoA catabolic process   
27                                                                     coenzyme A metabolic process   
28                                                                UDP-D-galactose metabolic process   
29                                                                  glucose transmembrane transport   
30                                                               UDP-galactose biosynthetic process   
31                                                  regulation of protein homodimerization activity   
32                                                regulation of response to reactive oxygen species   
33                                                            cellular response to interferon-alpha   
34  antigen processing and presentation of exogenous peptide antigen via MHC class I, TAP-dependent   
35                                                              P-type calcium transporter activity   
36                                                                           obsolete membrane part   
37                                          RNA splicing, via endonucleolytic cleavage and ligation   
38                                                                            

In [64]:
hallucinatons(df, DAVINCI)

NAME  \
0                                obsolete Gly-X carboxypeptidase activity   
1                                                         phosphorylation   
2                                     Holliday junction resolvase complex   
3                                   double-stranded telomeric DNA binding   
4                                                     histone acetylation   
5                                                             protein tag   
6                          cysteine-type endopeptidase inhibitor activity   
7                                             obsolete electron transport   
8                                                     cytosolic transport   
9                                                  endopeptidase activity   
10                              phosphatidylserine decarboxylase activity   
11                              obsolete transcription activator activity   
12                                                C-X-C chemokine binding   
13                                                        DNA replication   
14                                                        obsolete lectin   
15                phosphatidylinositol trisphosphate phosphatase activity   
16                                                        obsolete serpin   
17                             obsolete extracellular matrix glycoprotein   
18             obsolete calcium-dependent cell adhesion molecule activity   
19                                                    cytokine production   
20                                             obsolete vesicle transport   
21                                          receptor-mediated endocytosis   
22                obsolete transcription factor activity, protein binding   
23                                                       limb development   
24                                               obsolete cytochrome P450   
25                                                            translation   
26                                      glycoprotein biosynthetic process   
27                                               sterol catabolic process   
28                                         bile acid biosynthetic process   
29                                                obsolete plasma protein   
30                                           obsolete matrilysin activity   
31                                                           obsolete RNA   
32                           DNA replication-dependent chromatin assembly   
33                               obsolete small nuclear ribonucleoprotein   
34                               obsolete covalent chromatin modification   
35                                         obsolete ATP catabolic process   
36                              epidermal growth factor receptor activity   
37                                                      obsolete collagen   
38                                                            cell growth   
39                                                     protein processing   
40                            inward rectifier potassium channel activity   
41                                              activin receptor activity   
42                                                   nucleotide transport   
43                                          metalloendopeptidase activity   
44   biotin-[propionyl-CoA-carboxylase (ATP-hydrolyzing)] ligase activity   
45                                    obsolete coenzyme metabolic process   
46                                                         actin filament   
47                             adenyl-nucleotide exchange factor activity   
48                                             microtubule polymerization   
49                                          activation of GTPase activity   
50                                     structural constituent of ribosome   
51                                        cell cycle checkpoint s

## New Annotations

In [65]:
endocytosis = df.query(f"{GENESET} == 'endocytosis-0'").sort_values("similarity", ascending=False)
terms_summary(endocytosis)

id  \
0                                                                                                                                                                                                                                                                                                                                                  GO:0006907   
1                                                                                                                                                                                                                                                                                                                                                  GO:0006897   
2                                                                                                                                                                                                                                                                                                                                                  GO:0044351   
3                                                                                                                                                                                                                                                                                                                                                  GO:0016192   
4                                                                                                                                                                                                                                                                                                                                                  GO:0030100   
5                                                                                                                                                                                                                                                                                                                                                  GO:0006810   
6                                                                                                                                                                                                                                                                                                                                                  GO:0051234   
7                                                                                                                                                                                                                                                                                                                                                  GO:0045807   
8                                                                                                                                                                                                                                                                                                                                                  GO:0060627   
9                                                                                                                                                                                                                                                                                                                                                  GO:0051179   
10                                                                                                                                                                                                                                                                                                                                                 GO:0031410   
11                                                                                                             

### New Annotations

in 2022-03-24, GO `molecular sequesting` only had 6 genes annotated; this increased to 30 in 2023.
If these are past the LLM training date then we would not expect these to influence results. Additionally,


In [66]:
sequestering = df.query(f"{GENESET} == 'molecular sequestering-0'").sort_values("similarity", ascending=False)
sequestering[eval_summary_cols]                                                           

has top hit  in top 5  in top 10  size overlap  similarity  num terms  \
2188         True      True       True            26        1.00         26   
2189         True      True       True             9        0.28         15   
2179         True      True       True             2        0.07          6   
2178        False     False      False             1        0.04          8   
2184         True     False       True             1        0.03         19   
2185        False     False      False             1        0.03         10   
2176        False     False      False             1        0.03          8   
2191        False     False      False             1        0.02         30   
2192         True     False      False            26        0.01       2570   
2183        False     False      False             0        0.00          6   
2177        False     False      False             0        0.00          7   
2182        False     False      False             0        0.00          5   
2186        False     False      False             0        0.00         19   
2187        False     False      False             0        0.00         13   
2181        False     False      False             0        0.00          3   
2180        False     False      False             0        0.00          3   
2190        False     False      False             0        0.00         29   

      num GO terms  nr size overlap  nr similarity  mean p value  min p value  \
2188            26               10           1.00          0.02     1.83e-93   
2189            15                2           0.11          0.41     1.83e-93   
2179             4                1           0.08          0.50     1.83e-93   
2178             3                0           0.00          0.67     1.97e-03   
2184             6                0           0.00          0.83     1.83e-93   
2185             6                0           0.00          0.83     2.83e-38   
2176             8                1           0.06          0.88     4.66e-04   
2191            30                0           0.00          0.97     4.71e-02   
2192          2526                0           0.00          0.99     1.83e-93   
2183             2                0           0.00          1.00     1.00e+00   
2177             7                0           0.00          1.00     1.00e+00   
2182             2                0           0.00          1.00     1.00e+00   
2186             9                0           0.00          1.00     1.00e+00   
2187             8                0           0.00          1.00     1.00e+00   
2181             3                0           0.00          1.00     1.00e+00   
2180             2                0           0.00          1.00     1.00e+00   
2190            29                0           0.00          1.00     1.00e+00   

      max p value  proportion significant  num novel  
2188         0.05                    1.00          0  
2189         1.00                    0.60          0  
2179         1.00                    0.50          0  
2178         1.00                    0.33          0  
2184         1.00                    0.17          1  
2185         1.00                    0.17          0  
2176         1.00                    0.12          0  
2191         1.00                    0.03          1  
2192         1.00                    0.01          0  
2183         1.00                    0.00          1  
2177         1.00                    0.00          0  
2182         1.00                    0.00          0  
2186         1.00                    0.00          1  
2187         1.00                    0.00          1  
2181         1.00                    0.00          0  
2180         1.00                    0.00          0  
2190         1.00                    0.00         17

In [67]:
terms_summary(sequestering)

id  \
0                                                                                                                                                            GO:0140313   
1                                                                                                                                                            GO:0140311   
2                                                                                                                                                            GO:0140487   
3                                                                                                                                                            GO:0048519   
4                                                                                                                                                            GO:0006950   
5                                                                                                                                                            GO:0048523   
6                                                                                                                                                            GO:0140678   
7                                                                                                                                                            GO:0048585   
8                                                                                                                                                            GO:0036316   
9                                                                                                                                                            GO:0140315   
10                                                                                                                                                           GO:0140486   
11                                                                                                                                                           GO:0140610   
12                                                                                                                                                           GO:0005488   
13                                                                                                                                                           GO:0051235   
14                                                                                                                                                           GO:0002682   
15                                                                                                                                                           GO:0010629   
16                                                                                                                                                           GO:0032937   
17                                                                                                                                                           GO:2000639   
18                                                                                                                                                           GO:0009968   
19                                                                                                                                                           GO:0000041   
20                                                                                                                                                           GO:1901222   
21                                                                                                                                                           GO:0051651   
22                                                                                                                                                           GO:0010648   
23                                                           

## IGRB

This gene set contains genes previously annotated to IGRB, many of which have been since removed

In [68]:
igrb = df.query(f"{GENESET} == 'ig-receptor-binding-2022-0'").sort_values("similarity", ascending=False)
terms_summary(igrb)

id  \
0                                                                                                                                                                                                                                                                                                                                                                                              GO:0019814   
1                                                                                                                                                                                                                                                                                                                                                                                              GO:0009897   
2                                                                                                                                                                                                                                                                                                                                                                                              GO:0098552   
3                                                                                                                                                                                                                                                                                                                                                                                              GO:0002250   
4                                                                                                                                                                                                                                                                                                                                                                                              GO:0009986   
5                                                                                                                                                                                                                                                                                                                                                                                              GO:0006955   
6                                                                                                                                                                                                                                                                                                                                                                                              GO:0002376   
7                                                                                                                                                                                                                                                                                                                                                                                              GO:0005886   
8                                                                                                                                                                                                                                                                                                                                                                                              GO:0071944   
9                                                                                                                                                                                                                                                                                                                                                                                              GO:0003823   
10                      

## Summaries

In [69]:
objs = []
for c in comps:
    for m, payload in c.payloads.items():
        if payload.summary:
            objs.append({"model": c.model, "geneset": c.name, "method": m, "summary": payload.summary})

In [70]:
sdf = pd.DataFrame(objs)

In [71]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
sdf

model                                                 geneset  \
0     None                                                   EDS-0   
1     None                                                   EDS-0   
2     None                                                   EDS-0   
3     None                                                   EDS-0   
4     None                                                   EDS-0   
5     None                                                   EDS-0   
6     None                                                   EDS-0   
7     None                                                   EDS-0   
8     None                                                   EDS-0   
9     None                                                   EDS-0   
10    None                                                   EDS-0   
11    None                                                   EDS-0   
12    None                                                   EDS-1   
13    None                                                   EDS-1   
14    None                                                   EDS-1   
15    None                                                   EDS-1   
16    None                                                   EDS-1   
17    None                                                   EDS-1   
18    None                                                   EDS-1   
19    None                                                   EDS-1   
20    None                                                   EDS-1   
21    None                                                   EDS-1   
22    None                                                   EDS-1   
23    None                                                   EDS-1   
24    None                                                    FA-0   
25    None                                                    FA-0   
26    None                                                    FA-0   
27    None                                                    FA-0   
28    None                                                    FA-0   
29    None                                                    FA-0   
30    None                                                    FA-0   
31    None                                                    FA-0   
32    None                                                    FA-0   
33    None                                                    FA-0   
34    None                                                    FA-0   
35    None                                                    FA-0   
36    None                                                    FA-1   
37    None                                                    FA-1   
38    None                                                    FA-1   
39    None                                                    FA-1   
40    None                                                    FA-1   
41    None                                                    FA-1   
42    None                                                    FA-1   
43    None                                                    FA-1   
44    None                                                    FA-1   
45    None                                                    FA-1   
46    None                                                    FA-1   
47    None                                                    FA-1   
48    None                                 HALLMARK_ADIPOGENESIS-0   
49    None                                 HALLMARK_ADIPOGENESIS-0   
50    None                                 HALLMARK_ADIPOGENESIS-0   
51    None                                 HALLMARK_ADIPOGENESIS-0   
52    None                                 HALLMARK_ADIPOGENESIS-0   
53    None                                 HALLMARK_ADIPOGENESIS-0   
54    None                                 HALLMARK_ADIPOGENESIS-0   
55    None                                 HALLMARK_ADIPOGENESIS-0   
56    None     

In [ ]:
sdf.query("geneset == 'sensory ataxia-0'")